In [1]:
import pandas as pd
import numpy as np

from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import GridSearchCV
from sklearn.preprocessing import StandardScaler

from sklearn.metrics import mean_squared_error

import plotly.express as px

import mlflow
import mlflow.sklearn
from ydata_profiling import ProfileReport

import xgboost as xgb

from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope

D:\anaconda3\Lib\site-packages\numba\core\decorators.py:262: NumbaDeprecationWarning: numba.generated_jit is deprecated. Please see the documentation at: https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-generated-jit for more information and advice on a suitable replacement.
  warnings.warn(msg, NumbaDeprecationWarning)
D:\anaconda3\Lib\site-packages\visions\backends\shared\nan_handling.py:50: NumbaDeprecationWarning: The 'nopython' keyword argument was not supplied to the 'numba.jit' decorator. The implicit default value for this argument is currently False, but it will be changed to True in Numba 0.59.0. See https://numba.readthedocs.io/en/stable/reference/deprecation.html#deprecation-of-object-mode-fall-back-behaviour-when-using-jit for details.
  @nb.jit


In [2]:
# Assuming the script is located in the parent directory of the "data" folder.
data = pd.read_csv('data/application_record.csv')
record = pd.read_csv('data/credit_record.csv')

In [3]:
# find all users' account open month.
begin_month=pd.DataFrame(record.groupby(["ID"])["MONTHS_BALANCE"].agg(min))
begin_month=begin_month.rename(columns={'MONTHS_BALANCE':'begin_month'}) 

new_data=pd.merge(data,begin_month,how="left",on="ID") #merge to record data

In [4]:
data.head()

ID CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  CNT_CHILDREN  \
0  5008804           M            Y               Y             0   
1  5008805           M            Y               Y             0   
2  5008806           M            Y               Y             0   
3  5008808           F            N               Y             0   
4  5008809           F            N               Y             0   

   AMT_INCOME_TOTAL      NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
0          427500.0               Working               Higher education   
1          427500.0               Working               Higher education   
2          112500.0               Working  Secondary / secondary special   
3          270000.0  Commercial associate  Secondary / secondary special   
4          270000.0  Commercial associate  Secondary / secondary special   

     NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  DAYS_BIRTH  DAYS_EMPLOYED  \
0        Civil marriage   Rented apartment      -12005          -4542   
1        Civil marriage   Rented apartment      -12005          -4542   
2               Married  House / apartment      -21474          -1134   
3  Single / not married  House / apartment      -19110          -3051   
4  Single / not married  House / apartment      -19110          -3051   

   FLAG_MOBIL  FLAG_WORK_PHONE  FLAG_PHONE  FLAG_EMAIL OCCUPATION_TYPE  \
0           1                1           0           0             NaN   
1           1                1           0           0             NaN   
2           1                0           0           0  Security staff   
3           1                0           1           1     Sales staff   
4           1                0           1           1     Sales staff   

   CNT_FAM_MEMBERS  
0              2.0  
1              2.0  
2              2.0  
3              1.0  
4              1.0

In [94]:
profile = ProfileReport(data, title="Profiling Report")
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [95]:
record.head()

ID  MONTHS_BALANCE STATUS
0  5001711               0      X
1  5001711              -1      0
2  5001711              -2      0
3  5001711              -3      0
4  5001712               0      C

In [8]:
profile_record = ProfileReport(record, title="Profiling Report")
profile_record.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

STATUS Column

0: 1-29 days past due

1: 30-59 days past due

2: 60-89 days overdue 3: 90-119 days overdue

4: 120-149 days overdue

5: Overdue or bad debts, write-offs for more than 150 days

C: paid off that month

X: No loan for the month

In [5]:
    # Assuming 'record' is your DataFrame containing the 'STATUS' and 'dep_value' columns.
    record['dep_value'] = None
    record.loc[record['STATUS'].isin(['2', '3', '4', '5']), 'dep_value'] = 'Yes'

    cpunt=record.groupby('ID').count()
    cpunt['dep_value'][cpunt['dep_value'] > 0]='Yes' 
    cpunt['dep_value'][cpunt['dep_value'] == 0]='No' 
    cpunt = cpunt[['dep_value']]

    merge_data=pd.merge(new_data,cpunt,how='inner',on='ID')

In [57]:
# cpunt=record.groupby('ID').count()
# cpunt['dep_value'][cpunt['dep_value'] > 0]='Yes' 
# cpunt['dep_value'][cpunt['dep_value'] == 0]='No' 
# cpunt = cpunt[['dep_value']]

# merge_data=pd.merge(new_data,cpunt,how='inner',on='ID')
# # new_data['target']=new_data['dep_value']
# # new_data.loc[new_data['target']=='Yes','target']=1
# # new_data.loc[new_data['target']=='No','target']=0

In [6]:
# Assuming 'new_data' is your DataFrame.
# Check for missing values (NaN) in the DataFrame
print(merge_data.isna().sum())

# Drop rows with any NaN values
merge_data.dropna(inplace=True)

# Display the first few rows of the cleaned DataFrame
merge_data.head()

ID                         0
CODE_GENDER                0
FLAG_OWN_CAR               0
FLAG_OWN_REALTY            0
CNT_CHILDREN               0
AMT_INCOME_TOTAL           0
NAME_INCOME_TYPE           0
NAME_EDUCATION_TYPE        0
NAME_FAMILY_STATUS         0
NAME_HOUSING_TYPE          0
DAYS_BIRTH                 0
DAYS_EMPLOYED              0
FLAG_MOBIL                 0
FLAG_WORK_PHONE            0
FLAG_PHONE                 0
FLAG_EMAIL                 0
OCCUPATION_TYPE        11323
CNT_FAM_MEMBERS            0
begin_month                0
dep_value                  0
dtype: int64


ID CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  CNT_CHILDREN  \
2  5008806           M            Y               Y             0   
3  5008808           F            N               Y             0   
4  5008809           F            N               Y             0   
5  5008810           F            N               Y             0   
6  5008811           F            N               Y             0   

   AMT_INCOME_TOTAL      NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
2          112500.0               Working  Secondary / secondary special   
3          270000.0  Commercial associate  Secondary / secondary special   
4          270000.0  Commercial associate  Secondary / secondary special   
5          270000.0  Commercial associate  Secondary / secondary special   
6          270000.0  Commercial associate  Secondary / secondary special   

     NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  DAYS_BIRTH  DAYS_EMPLOYED  \
2               Married  House / apartment      -21474          -1134   
3  Single / not married  House / apartment      -19110          -3051   
4  Single / not married  House / apartment      -19110          -3051   
5  Single / not married  House / apartment      -19110          -3051   
6  Single / not married  House / apartment      -19110          -3051   

   FLAG_MOBIL  FLAG_WORK_PHONE  FLAG_PHONE  FLAG_EMAIL OCCUPATION_TYPE  \
2           1                0           0           0  Security staff   
3           1                0           1           1     Sales staff   
4           1                0           1           1     Sales staff   
5           1                0           1           1     Sales staff   
6           1                0           1           1     Sales staff   

   CNT_FAM_MEMBERS  begin_month dep_value  
2              2.0        -29.0        No  
3              1.0         -4.0        No  
4              1.0        -26.0        No  
5              1.0        -26.0        No  
6              1.0        -38.0        No

In [7]:
merge_data.columns

Index(['ID', 'CODE_GENDER', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'CNT_CHILDREN',
       'AMT_INCOME_TOTAL', 'NAME_INCOME_TYPE', 'NAME_EDUCATION_TYPE',
       'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'DAYS_BIRTH',
       'DAYS_EMPLOYED', 'FLAG_MOBIL', 'FLAG_WORK_PHONE', 'FLAG_PHONE',
       'FLAG_EMAIL', 'OCCUPATION_TYPE', 'CNT_FAM_MEMBERS', 'begin_month',
       'dep_value'],
      dtype='object')

In [8]:
# Now, we remove duplicates

data = merge_data.drop_duplicates('ID', keep='last')

# For credibility, we will double-check the data and see the total number of rows. There should be 438510

data.head()

ID CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  CNT_CHILDREN  \
2  5008806           M            Y               Y             0   
3  5008808           F            N               Y             0   
4  5008809           F            N               Y             0   
5  5008810           F            N               Y             0   
6  5008811           F            N               Y             0   

   AMT_INCOME_TOTAL      NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
2          112500.0               Working  Secondary / secondary special   
3          270000.0  Commercial associate  Secondary / secondary special   
4          270000.0  Commercial associate  Secondary / secondary special   
5          270000.0  Commercial associate  Secondary / secondary special   
6          270000.0  Commercial associate  Secondary / secondary special   

     NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  DAYS_BIRTH  DAYS_EMPLOYED  \
2               Married  House / apartment      -21474          -1134   
3  Single / not married  House / apartment      -19110          -3051   
4  Single / not married  House / apartment      -19110          -3051   
5  Single / not married  House / apartment      -19110          -3051   
6  Single / not married  House / apartment      -19110          -3051   

   FLAG_MOBIL  FLAG_WORK_PHONE  FLAG_PHONE  FLAG_EMAIL OCCUPATION_TYPE  \
2           1                0           0           0  Security staff   
3           1                0           1           1     Sales staff   
4           1                0           1           1     Sales staff   
5           1                0           1           1     Sales staff   
6           1                0           1           1     Sales staff   

   CNT_FAM_MEMBERS  begin_month dep_value  
2              2.0        -29.0        No  
3              1.0         -4.0        No  
4              1.0        -26.0        No  
5              1.0        -26.0        No  
6              1.0        -38.0        No

In [9]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 25134 entries, 2 to 36456
Data columns (total 20 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ID                   25134 non-null  int64  
 1   CODE_GENDER          25134 non-null  object 
 2   FLAG_OWN_CAR         25134 non-null  object 
 3   FLAG_OWN_REALTY      25134 non-null  object 
 4   CNT_CHILDREN         25134 non-null  int64  
 5   AMT_INCOME_TOTAL     25134 non-null  float64
 6   NAME_INCOME_TYPE     25134 non-null  object 
 7   NAME_EDUCATION_TYPE  25134 non-null  object 
 8   NAME_FAMILY_STATUS   25134 non-null  object 
 9   NAME_HOUSING_TYPE    25134 non-null  object 
 10  DAYS_BIRTH           25134 non-null  int64  
 11  DAYS_EMPLOYED        25134 non-null  int64  
 12  FLAG_MOBIL           25134 non-null  int64  
 13  FLAG_WORK_PHONE      25134 non-null  int64  
 14  FLAG_PHONE           25134 non-null  int64  
 15  FLAG_EMAIL           25134 non-null 

In [10]:
# Now, we remove OCCUPATION_TYPE. As we said, it have too many missed data
# In addition, we will get rid of FLAG_MOBIL, FLAG_WORK_PHONE, FLAG_PHONE and FLAG_EMAIL. 
# These parameters do not affect in any way whether a person is creditworthy or not.

data.drop(['ID','FLAG_WORK_PHONE','FLAG_PHONE','FLAG_EMAIL'], axis=1, inplace=True) 

In [11]:
data.columns

Index(['CODE_GENDER', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'CNT_CHILDREN',
       'AMT_INCOME_TOTAL', 'NAME_INCOME_TYPE', 'NAME_EDUCATION_TYPE',
       'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'DAYS_BIRTH',
       'DAYS_EMPLOYED', 'FLAG_MOBIL', 'OCCUPATION_TYPE', 'CNT_FAM_MEMBERS',
       'begin_month', 'dep_value'],
      dtype='object')

In [12]:
# Now, it's time to parse the data type object. 
# It is necessary to determine whether they have any value for evaluating credit, 
# and also to evaluate the possibility of converting data to a numeric type.

objects_data = pd.DataFrame(data.dtypes =='object').reset_index()
object_type = objects_data[objects_data[0] == True]['index']
object_type

0             CODE_GENDER
1            FLAG_OWN_CAR
2         FLAG_OWN_REALTY
5        NAME_INCOME_TYPE
6     NAME_EDUCATION_TYPE
7      NAME_FAMILY_STATUS
8       NAME_HOUSING_TYPE
12        OCCUPATION_TYPE
15              dep_value
Name: index, dtype: object

In [13]:
# First, let's find out what data the columns contain so that we can properly train our model. 
# Since we see that there are quite a lot of important parameters, 
# we will try to translate all this into numerical values.

a = data[object_type]['CODE_GENDER'].value_counts()
b = data[object_type]['FLAG_OWN_CAR'].value_counts()
c = data[object_type]['FLAG_OWN_REALTY'].value_counts()
d = data[object_type]['NAME_INCOME_TYPE'].value_counts()
e = data[object_type]['NAME_EDUCATION_TYPE'].value_counts()
f = data[object_type]['NAME_FAMILY_STATUS'].value_counts()
g = data[object_type]['NAME_HOUSING_TYPE'].value_counts()
h = data[object_type]['dep_value'].value_counts()

print('\n',a,'\n\n',b,'\n\n',c,'\n\n',d,'\n\n',e,'\n\n',f,'\n\n', g, '\n\n', h)


 F    15630
M     9504
Name: CODE_GENDER, dtype: int64 

 N    14618
Y    10516
Name: FLAG_OWN_CAR, dtype: int64 

 Y    16461
N     8673
Name: FLAG_OWN_REALTY, dtype: int64 

 Working                 15622
Commercial associate     7052
State servant            2437
Pensioner                  13
Student                    10
Name: NAME_INCOME_TYPE, dtype: int64 

 Secondary / secondary special    16808
Higher education                  7132
Incomplete higher                  993
Lower secondary                    187
Academic degree                     14
Name: NAME_EDUCATION_TYPE, dtype: int64 

 Married                 17509
Single / not married     3445
Civil marriage           2133
Separated                1467
Widow                     580
Name: NAME_FAMILY_STATUS, dtype: int64 

 House / apartment      22102
With parents            1430
Municipal apartment      812
Rented apartment         439
Office apartment         199
Co-op apartment          152
Name: NAME_HOUSING_TYPE, dty

In [14]:
# Now, let's convert all non-numeric data to numeric data using LabelEncoder().
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
for x in data:
    if data[x].dtypes == 'object' and x != 'dep_value':
        data[x] = le.fit_transform(data[x])

In [15]:
data.head(10)

CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  CNT_CHILDREN  \
2             1             1                1             0   
3             0             0                1             0   
4             0             0                1             0   
5             0             0                1             0   
6             0             0                1             0   
10            1             1                1             0   
11            1             1                1             0   
12            1             1                1             0   
13            1             1                1             0   
14            1             1                1             0   

    AMT_INCOME_TOTAL  NAME_INCOME_TYPE  NAME_EDUCATION_TYPE  \
2           112500.0                 4                    4   
3           270000.0                 0                    4   
4           270000.0                 0                    4   
5           270000.0                 0                    4   
6           270000.0                 0                    4   
10          270000.0                 4                    1   
11          270000.0                 4                    1   
12          135000.0                 0                    4   
13          135000.0                 0                    4   
14          135000.0                 0                    4   

    NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  DAYS_BIRTH  DAYS_EMPLOYED  \
2                    1                  1      -21474          -1134   
3                    3                  1      -19110          -3051   
4                    3                  1      -19110          -3051   
5                    3                  1      -19110          -3051   
6                    3                  1      -19110          -3051   
10                   1                  1      -16872           -769   
11                   1                  1      -16872           -769   
12                   1                  1      -17778          -1194   
13                   1                  1      -17778          -1194   
14                   1                  1      -17778          -1194   

    FLAG_MOBIL  OCCUPATION_TYPE  CNT_FAM_MEMBERS  begin_month dep_value  
2            1               16              2.0        -29.0        No  
3            1               14              1.0         -4.0        No  
4            1               14              1.0        -26.0        No  
5            1               14              1.0        -26.0        No  
6            1               14              1.0        -38.0        No  
10           1                0              2.0         -5.0        No  
11           1                0              2.0        -42.0        No  
12           1                8              2.0        -17.0        No  
13           1                8              2.0        -16.0        No  
14           1                8              2.0         -8.0        No

In [16]:
data.columns

Index(['CODE_GENDER', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'CNT_CHILDREN',
       'AMT_INCOME_TOTAL', 'NAME_INCOME_TYPE', 'NAME_EDUCATION_TYPE',
       'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'DAYS_BIRTH',
       'DAYS_EMPLOYED', 'FLAG_MOBIL', 'OCCUPATION_TYPE', 'CNT_FAM_MEMBERS',
       'begin_month', 'dep_value'],
      dtype='object')

In [130]:
selected_columns = ['CODE_GENDER', 'FLAG_OWN_CAR', 'FLAG_OWN_REALTY', 'CNT_CHILDREN',
       'AMT_INCOME_TOTAL', 'NAME_INCOME_TYPE', 'NAME_EDUCATION_TYPE',
       'NAME_FAMILY_STATUS', 'NAME_HOUSING_TYPE', 'DAYS_BIRTH',
       'DAYS_EMPLOYED', 'CNT_FAM_MEMBERS', 'begin_month']

for each_name in selected_columns:
    each_count = data.groupby([each_name, 'dep_value']).size().reset_index(name='Count')

    fig = px.bar(each_count, x=f'{each_name}', y='Count', color='dep_value', barmode='group')

    fig.show()

In [17]:
# Before continuing our research, let's count how many people have paid off their loans, 
# and how many still have debts.

data['dep_value'].value_counts(normalize = True)

# As you can see, we are seeing the phenomenon of oversampling: 
# 99% of people have paid off their debt, 1% have not yet done so. 
# This means that our sample may not be representative, and the machine will not be able to correctly learn 
# to determine who should be given a credit and who should not. 
# To fix the problem, we need to merge both sets of our data.

No     0.98321
Yes    0.01679
Name: dep_value, dtype: float64

In [18]:
# Assuming 'data' is your DataFrame containing the 'dep_value' column.
label_encoder = LabelEncoder()

# Map 'Yes' to 1 and 'No' to 0 in the 'dep_value' column
data['dep_value'] = label_encoder.fit_transform(data['dep_value'])

# Now 'dep_value' column contains 0s and 1s, where 0 represents 'No' and 1 represents 'Yes'

In [21]:
# Since we can lose a huge amount of data when reducing people without debt, and reduce the accuracy of the machine, 
# we will choose the second path. 
# At first, the thought comes to us that we will simply have to duplicate existing data, 
# but SMOTE (Synthetic Minority Over-sampling Technique) comes to the rescue. 
# This is an algorithm that will help us "generate" new data and avoid overfitting the model.

X = data.iloc[:,1:-1] # X value contains all the variables except labels
y = data.iloc[:,-1] # these are the labels
y

2        0
3        0
4        0
5        0
6        0
        ..
36452    1
36453    1
36454    1
36455    1
36456    1
Name: dep_value, Length: 25134, dtype: int32

In [22]:
# First, we divide the data in half: 
# into those that will be used to train the model 
# and those that will be used to predict approval.

# Usually, it is customary to divide the data as follows: 
# 70% is used for training the model, and 30% for testing.

from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3)

In [23]:
# Next, we will use the SMOTE algorithm to make up for the lack of data

from imblearn.over_sampling import SMOTE

oversample = SMOTE()
X_balanced, y_balanced = oversample.fit_resample(X_train, y_train)
X_test_balanced, y_test_balanced = oversample.fit_resample(X_test, y_test)

In [24]:
# Let's compare the amount of data before and after the SMOTE algorithm. 
# As we can see, now the number of debtors 
# and people who have no debts (or do not have a credit history) are equal, 
# and we can safely train our model.

a = y_train.value_counts()
b = y_balanced.value_counts()
print(a, "\n\n", b)

0    17316
1      277
Name: dep_value, dtype: int64 

 0    17316
1    17316
Name: dep_value, dtype: int64


In [25]:
a = y_test.value_counts()
b = y_test_balanced.value_counts()
print(a, "\n\n", b)

0    7396
1     145
Name: dep_value, dtype: int64 

 0    7396
1    7396
Name: dep_value, dtype: int64


In [ ]:
# MLflow tracking

In [32]:
mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment("test")

<Experiment: artifact_location='file:///D:/Project Pycharm/creditcard_approval_prediction/mlruns/1', creation_time=1690009378628, experiment_id='1', last_update_time=1690009378628, lifecycle_stage='active', name='test', tags={}>

In [33]:
train = xgb.DMatrix(X_balanced, label=y_balanced)
validation = xgb.DMatrix(X_test_balanced, label=y_test_balanced)

In [30]:
def objective(params):
    with mlflow.start_run():
        num_boost_round = 500
        early_stopping_rounds = 50
        
        mlflow.log_params(params)
        mlflow.log_param('num_boost_round', num_boost_round)
        mlflow.log_param('early_stopping_rounds', early_stopping_rounds)
        mlflow.log_param('train_data_name', 'green_tripdata_2021-01.parquet')
        mlflow.log_param('validation_data_name', 'green_tripdata_2021-02.parquet')
        mlflow.set_tag('model', 'xgboost')

        booster = xgb.train(
            params = params,
            dtrain = train,
            evals = [(validation, "validation")],
            num_boost_round = num_boost_round,
            early_stopping_rounds = early_stopping_rounds
        )
        
        y_pred = booster.predict(validation)
        rmse = mean_squared_error(y_test_balanced, y_pred, squared=False)
        mlflow.log_metric('rmse', rmse)
        return {'loss': rmse, 'status': STATUS_OK}

In [34]:
grid_search = {
    'max_depth': scope.int(hp.quniform('max_depth', 4, 100, 1)),
    'reg_alpha': hp.loguniform('reg_alpha', -5, -1),
    'reg_lambda': hp.loguniform('reg_lambda', -6, -1),
    'min_child': hp.loguniform('min_child', -1, 3),
    'seed': 111,
    'objective': 'reg:linear'
}

In [35]:
best_model = fmin(
    fn=objective,
    space=grid_search,
    algo=tpe.suggest,
    max_evals=30,
    trials=Trials()
)

[14:33:14] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0fdc6d574b9c0d168-1\xgboost\xgboost-ci-windows\src\objective\regression_obj.cu:213: reg:linear is now deprecated in favor of reg:squarederror.
[14:33:14] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0fdc6d574b9c0d168-1\xgboost\xgboost-ci-windows\src\learner.cc:767: 
Parameters: { "min_child" } are not used.

[0]	validation-rmse:0.42796                                                                                            
[1]	validation-rmse:0.39900                                                                                            
[2]	validation-rmse:0.39108                                                                                            
[3]	validation-rmse:0.39245                                                                                            
[4]	validation-rmse:0.39756                                                               

[9]	validation-rmse:0.40610                                                                                            
[10]	validation-rmse:0.40740                                                                                           
[11]	validation-rmse:0.40806                                                                                           
[12]	validation-rmse:0.40807                                                                                           
[13]	validation-rmse:0.40806                                                                                           
[14]	validation-rmse:0.40790                                                                                           
[15]	validation-rmse:0.40773                                                                                           
[16]	validation-rmse:0.40745                                                                                           
[17]	validation-rmse:0.40750            

[21]	validation-rmse:0.31865                                                                                           
[22]	validation-rmse:0.31660                                                                                           
[23]	validation-rmse:0.31557                                                                                           
[24]	validation-rmse:0.31522                                                                                           
[25]	validation-rmse:0.31522                                                                                           
[26]	validation-rmse:0.31595                                                                                           
[27]	validation-rmse:0.31425                                                                                           
[28]	validation-rmse:0.31366                                                                                           
[29]	validation-rmse:0.31497            

[89]	validation-rmse:0.29189                                                                                           
[90]	validation-rmse:0.29154                                                                                           
[91]	validation-rmse:0.29139                                                                                           
[92]	validation-rmse:0.29052                                                                                           
[93]	validation-rmse:0.29049                                                                                           
[94]	validation-rmse:0.29026                                                                                           
[95]	validation-rmse:0.29029                                                                                           
[96]	validation-rmse:0.28984                                                                                           
[97]	validation-rmse:0.28971            

[157]	validation-rmse:0.27989                                                                                          
[158]	validation-rmse:0.27987                                                                                          
[159]	validation-rmse:0.27961                                                                                          
[160]	validation-rmse:0.27930                                                                                          
[161]	validation-rmse:0.27898                                                                                          
[162]	validation-rmse:0.27868                                                                                          
[163]	validation-rmse:0.27865                                                                                          
[164]	validation-rmse:0.27857                                                                                          
[165]	validation-rmse:0.27848           

...

[338]	validation-rmse:0.25696                                                                                          
[339]	validation-rmse:0.25696                                                                                          
[340]	validation-rmse:0.25698                                                                                          
[341]	validation-rmse:0.25702                                                                                          
[342]	validation-rmse:0.25681                                                                                          
[343]	validation-rmse:0.25682                                                                                          
[344]	validation-rmse:0.25686                                                                                          
[345]	validation-rmse:0.25692                                                                                          
[346]	validation-rmse:0.25684           

[406]	validation-rmse:0.25108                                                                                          
[407]	validation-rmse:0.25099                                                                                          
[408]	validation-rmse:0.25076                                                                                          
[409]	validation-rmse:0.25064                                                                                          
[410]	validation-rmse:0.25042                                                                                          
[411]	validation-rmse:0.25040                                                                                          
[412]	validation-rmse:0.25029                                                                                          
[413]	validation-rmse:0.25017                                                                                          
[414]	validation-rmse:0.25003           

[474]	validation-rmse:0.24720                                                                                          
[475]	validation-rmse:0.24709                                                                                          
[476]	validation-rmse:0.24687                                                                                          
[477]	validation-rmse:0.24677                                                                                          
[478]	validation-rmse:0.24668                                                                                          
[479]	validation-rmse:0.24662                                                                                          
[480]	validation-rmse:0.24653                                                                                          
[481]	validation-rmse:0.24648                                                                                          
[482]	validation-rmse:0.24639           

[38]	validation-rmse:0.43233                                                                                           
[39]	validation-rmse:0.43233                                                                                           
[40]	validation-rmse:0.43233                                                                                           
[41]	validation-rmse:0.43233                                                                                           
[42]	validation-rmse:0.43233                                                                                           
[43]	validation-rmse:0.43233                                                                                           
[44]	validation-rmse:0.43233                                                                                           
[45]	validation-rmse:0.43233                                                                                           
[46]	validation-rmse:0.43233            

[50]	validation-rmse:0.42153                                                                                           
[51]	validation-rmse:0.42152                                                                                           
[14:37:09] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0fdc6d574b9c0d168-1\xgboost\xgboost-ci-windows\src\objective\regression_obj.cu:213: reg:linear is now deprecated in favor of reg:squarederror.
[14:37:09] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-0fdc6d574b9c0d168-1\xgboost\xgboost-ci-windows\src\learner.cc:767: 
Parameters: { "min_child" } are not used.

[0]	validation-rmse:0.42908                                                                                            
[1]	validation-rmse:0.40068                                                                                            
[2]	validation-rmse:0.39619                                                               

In [36]:
# Train the Best Model

In [37]:
import xgboost as xgb

from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope

In [38]:
mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment("test")

<Experiment: artifact_location='file:///D:/Project Pycharm/creditcard_approval_prediction/mlruns/1', creation_time=1690009378628, experiment_id='1', last_update_time=1690009378628, lifecycle_stage='active', name='test', tags={}>

In [39]:
#We took the best params from the MLflow interface and copien them here

best_params = {
     
}

mlflow.xgboost.autolog()

booster = xgb.train(
    params = best_params,
    dtrain = train,
    evals = [(validation, "validation")],
    num_boost_round = 500,
    early_stopping_rounds = 50,
)

2023/07/22 14:37:31 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID 'a10c1911800c4fb1b154b850d2a9c133', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current xgboost workflow


[0]	validation-rmse:0.45890
[1]	validation-rmse:0.42932
[2]	validation-rmse:0.40885
[3]	validation-rmse:0.39168
[4]	validation-rmse:0.37154
[5]	validation-rmse:0.36554
[6]	validation-rmse:0.35413
[7]	validation-rmse:0.34737
[8]	validation-rmse:0.34546
[9]	validation-rmse:0.33990
[10]	validation-rmse:0.33391
[11]	validation-rmse:0.33280
[12]	validation-rmse:0.33147
[13]	validation-rmse:0.32733
[14]	validation-rmse:0.32246
[15]	validation-rmse:0.32279
[16]	validation-rmse:0.31953
[17]	validation-rmse:0.31934
[18]	validation-rmse:0.31863
[19]	validation-rmse:0.31799
[20]	validation-rmse:0.31621
[21]	validation-rmse:0.31529
[22]	validation-rmse:0.31324
[23]	validation-rmse:0.31240
[24]	validation-rmse:0.31168
[25]	validation-rmse:0.31015
[26]	validation-rmse:0.30967
[27]	validation-rmse:0.30965
[28]	validation-rmse:0.30715
[29]	validation-rmse:0.30686
[30]	validation-rmse:0.30593
[31]	validation-rmse:0.30522
[32]	validation-rmse:0.30437
[33]	validation-rmse:0.30331
[34]	validation-rmse:0.3

[276]	validation-rmse:0.26526
[277]	validation-rmse:0.26522
[278]	validation-rmse:0.26514
[279]	validation-rmse:0.26502
[280]	validation-rmse:0.26493
[281]	validation-rmse:0.26492
[282]	validation-rmse:0.26495
[283]	validation-rmse:0.26495
[284]	validation-rmse:0.26495
[285]	validation-rmse:0.26485
[286]	validation-rmse:0.26484
[287]	validation-rmse:0.26476
[288]	validation-rmse:0.26471
[289]	validation-rmse:0.26464
[290]	validation-rmse:0.26461
[291]	validation-rmse:0.26459
[292]	validation-rmse:0.26447
[293]	validation-rmse:0.26446
[294]	validation-rmse:0.26441
[295]	validation-rmse:0.26440
[296]	validation-rmse:0.26433
[297]	validation-rmse:0.26439
[298]	validation-rmse:0.26439
[299]	validation-rmse:0.26437
[300]	validation-rmse:0.26437
[301]	validation-rmse:0.26437
[302]	validation-rmse:0.26433
[303]	validation-rmse:0.26427
[304]	validation-rmse:0.26427
[305]	validation-rmse:0.26424
[306]	validation-rmse:0.26419
[307]	validation-rmse:0.26406
[308]	validation-rmse:0.26391
[309]	vali

2023/07/22 14:37:50 WARNING mlflow.xgboost: Failed to infer model signature: could not sample data to infer model signature: please ensure that autologging is enabled before constructing the dataset.
2023/07/22 14:38:12 WARNING mlflow.utils.autologging_utils: MLflow autologging encountered a warning: "D:\anaconda3\Lib\site-packages\_distutils_hack\__init__.py:33: UserWarning: Setuptools is replacing distutils."


In [ ]:
key="???"
if best_params.get(key):
    print(best_params.get(key))
else:
    print("no value")

In [ ]:
pd.DataFrame.from_dict([best_params])

In [ ]:
y_pred = booster.predict(validation)

rmse = mean_squared_error(y_val, y_pred, squared=False)
rmse

In [ ]:
with open('models/moodel.bin', 'wb') as f_out:
    pickle.dump(booster, f_out)

In [ ]:
with open('preprocessing/process_dataframe.bin', 'wb') as f_out:
    pickle.dump(process_dataframe, f_out)

In [ ]:
mlflow.set_experiment("test")
with mlflow.start_run():
    best_params = {

    }
    
    mlflow.log_params(best_params)
    mlflow.log_param('train_data_name', 'green_tripdata_2022-01.parquet')
    mlflow.log_param('validation_data_name', 'green_tripdata_2022-02.parquet')
    mlflow.set_tag('model', 'xgboost')
    
    booster = xgb.train(
    params = best_params,
    dtrain = train,
    evals = [(validation, "validation")],
    num_boost_round = 500,
    early_stopping_rounds = 50,
    )
    
    mlflow.xgboost.log_model(booster, artifact_path='mlflow_models')
    mlflow.log_artifact('preprocessing/process_dataframe.bin', artifact_path='preprocessing')
    

In [ ]:
logged_model = 'runs:???'
loaded_model = mlflow.pyfunc.load_model(logged_model)

In [ ]:
type(loaded_model)

In [ ]:
y_preds = loaded_model.predict(X_val)

In [ ]:
mean_squared_error(y_preds, y_val, squared=False)

In [ ]:
y_preds

In [ ]:
print(loaded_model.metadata.get_model_info())

In [ ]:
mlflow.sklearn.autolog()

for algorithm in (LinearSVR, RandomForestRegressor, GradientBoostingRegressor):
    with mlflow.start_run():
        mlflow.log_param('train_data_name', 'green_tripdata_2022-01.parquet')
        mlflow.log_param('validation_data_name', 'green_tripdata_2022-02.parquet')
        mlflow.log_artifact('preprocessing/process_dataframe.bin', artifact_path='preprocessing')
        model = algorithm()
        model.fit(X_train, y_train)
        
        preds = model.predict(X_val)
        rmse = mean_squared_error(preds, y_val, squared=False)
        mlflow.log_metric("rmse", rmse)

In [ ]:
from mlflow.tracking import MlflowClient
from mlflow.entities import ViewType

In [ ]:
MLFLOW_URI = "sqlite:///mlflow.db"

In [ ]:
client = MlflowClient(MLFLOW_URI)

In [ ]:
client.list_experiments()

In [ ]:
client.create_experiment(name = 'new-experimet')

In [ ]:
client.list_experiments()

In [ ]:
runs = client.search_runs(
    experiment_ids='1',
    run_view_type=ViewType.ACTIVE_ONLY,
    filter_string='metrics.rmse < 7',
    max_results=5,
    order_by=["metrics.rmse ASC"],
)

In [ ]:
for run in runs:
    print(f"run_id:{run.info.run_id}, metrics:{run.data.metrics['rmse']}")

In [ ]:
# X_balanced, y_balanced = oversample.fit_resample(X_train, y_train)
# X_test_balanced, y_test_balanced = oversample.fit_resample(X_test, y_test)


# # Standardizing the data
# sc = StandardScaler()
# X_train = sc.fit_transform(X_train)
# X_test = sc.transform(X_test)

# # set up MLflow
# mlflow.set_experiment("CreditCardApprovalExperiment")

# with mlflow.start_run():
#     # log some basic information
#     mlflow.log_param("data_shape", data.shape)
#     mlflow.log_param("target_variable", "approved")

#     # define a model
#     model = RandomForestClassifier(random_state=42)

#     # define a grid of hyperparameters to search
#     hyperparameters = {
#         'n_estimators': [100, 200, 300],
#         'max_depth': [2, 4, 6],
#     }

#     # set up cross-validation grid search
#     grid_search = GridSearchCV(model, hyperparameters, cv=5, scoring='roc_auc')

#     # fit the model and tune hyperparameters
#     grid_search.fit(X_train, y_train)

#     # log the best parameters
#     mlflow.log_param("best_params", grid_search.best_params_)

#     # evaluate the best model on the test set
#     y_pred_proba = grid_search.predict_proba(X_test)[:, 1]
#     auc_roc = roc_auc_score(y_test, y_pred_proba)

#     # log the performance metric
#     mlflow.log_metric("auc_roc", auc_roc)

#     # log the model
#     mlflow.sklearn.log_model(grid_search.best_estimator_, "model")